In [2]:
import pyaudio
from six.moves import queue
import time

# 녹음용 값 
# 16khz
RATE = 16000
# 버퍼는 1600
CHUNK = int(RATE / 10)  # 100ms

class MicrophoneStream(object):
    """마이크 입력 클래스"""
    def __init__(self, rate, chunk):
        self._rate = rate
        self._chunk = chunk

        # 마이크 입력 버퍼 생성
        self._buff = queue.Queue()
        self.closed = True

    # 클래스 열면 발생함.
    def __enter__(self):
        # pyaudio 인터페이스 생성
        self._audio_interface = pyaudio.PyAudio()
        # 16비트, 모노로 마이크 열기
        # 여기서 _fill_buffer 함수가 바로 callback함수 인데
        # 실제 버퍼가 쌓이면 이곳이 호출된다.
        # 즉, _fill_buffer 마이크 입력을 _fill_buffer 콜백함수로 전달 받음
        self._audio_stream = self._audio_interface.open(
            format=pyaudio.paInt16,
            channels=1, rate=self._rate,
            input=True, frames_per_buffer=self._chunk,
            stream_callback=self._fill_buffer,
        )        
        self.closed = False
        return self

    def __exit__(self, type, value, traceback):
        # 클래스 종료시 발생
        # pyaudio 종료
        self._audio_stream.stop_stream()
        self._audio_stream.close()

        self.closed = True
        # Signal the generator to terminate so that the client's
        # streaming_recognize method will not block the process termination.
        self._buff.put(None)
        self._audio_interface.terminate()
    
    # 마이크 버퍼가 쌓이면(CHUNK = 1600) 이 함수 호출 됨. 
    def _fill_buffer(self, in_data, frame_count, time_info, status_flags):
        # 마이크 입력 받으면 큐에 넣고 리턴
        self._buff.put(in_data)
        return None, pyaudio.paContinue

    # 제너레이터 함수 
    def generator(self):
        #클래스 종료될 떄까지 무한 루프 돌림 
        while not self.closed:
            
            # 큐에 데이터를 기다림.
            # block 상태임.
            chunk = self._buff.get()

            # 데이터가 없다면 문제 있음
            if chunk is None:
                return

            # data에 마이크 입력 받기
            data = [chunk]

            # 추가로 받을 마이크 데이터가 있는지 체크 
            while True:
                try:
                    # 데이터가 더 있는지 체크
                    chunk = self._buff.get(block=False)
                    if chunk is None:
                        return
                    # 데이터 추가
                    data.append(chunk)
                except queue.Empty:
                    # 큐에 데이터가 더이상 없다면 break
                    break

            #마이크 데이터를 리턴해줌 
            yield b''.join(data)
# [END audio_stream]

def main():
    # 마이크 열기 
    with MicrophoneStream(RATE, CHUNK) as stream:
        # 마이크 데이터 핸들을 가져옴 
        audio_generator = stream.generator()
        with open("voice", "wb") as file:
        for i in range(1000):
            # 1000번만 마이크 데이터 가져오고 빠져나감.
'''
            for x in audio_generator:
                # 마이크 음성 데이터
                print(x)            
'''
            for x in audio_generator:
                file.write(x)
                time.sleep(0.001)

if __name__ == '__main__':
    main()


b'\x00\x00\x00\x00\xff\xff\x00\x00\x00\x00\x00\x00\x00\x00\xff\xff\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\xff\xff\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x01\x00\x00\x00\xff\xff\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\xff\xff\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x01\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x01\x00\x00\x00\x00\x00\x00\x00\x01\x00\x01\x00\x00\x00\x00\x00\x00\x00\xff\xff\x01\x00\x01\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x01\x00\x00\x00\x00\x00\x00\x00\x01\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\xff\xff\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\xff\xff\xff\xff\xff\xff\x00\x00\x00\x00\x00\x00\x00\x00\xff\xff\x00\x

b'\x00\x00\x00\x00\x01\x00\x01\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x01\x00\x01\x00\x01\x00\x00\x00\x00\x00\xff\xff\x00\x00\x00\x00\x00\x00\xff\xff\xff\xff\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x01\x00\x01\x00\x01\x00\x00\x00\xff\xff\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x01\x00\xff\xff\xff\xff\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x01\x00\x00\x00\xff\xff\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\xff\xff\x00\x00\x00\x00\x00\x00\x00\x00\x01\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\xff\xff\x01\x00\x01\x00\x00\x00\x00\x00\x00\x00\x00\x00\x01\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x01\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x01\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x01\x00\x00\x

b'\x08\x00\x07\x00\x06\x00\x03\x00\xfc\xff\xfc\xff\x04\x00\x10\x00\x03\x00\xf3\xff\xfb\xff\xf5\xff\xf3\xff\xf6\xff\xe2\xff\xd9\xff\xd9\xff\xd1\xff\xcd\xff\xd8\xff\xda\xff\xde\xff\xf2\xff\xe8\xff\xe7\xff\xf0\xff\xeb\xff\xf2\xff\x02\x00\x04\x00\xf6\xff\xef\xff\xe4\xff\xdf\xff\xe4\xff\xe7\xff\xe1\xff\xdc\xff\xe6\xff\xe2\xff\xd9\xff\xd9\xff\xd8\xff\xdc\xff\xdd\xff\xdd\xff\xdd\xff\xdd\xff\xe5\xff\xde\xff\xd3\xff\xd9\xff\xd7\xff\xdd\xff\xe0\xff\xd7\xff\xe1\xff\xec\xff\xf3\xff\x07\x00\x08\x00\xfa\xff\x02\x00\x12\x00\x11\x00\x12\x00\x15\x00\x18\x00"\x00\x1d\x00\x13\x00\x12\x00\x04\x00\x00\x00\x0f\x00\x0c\x00\x1a\x00*\x00\x1e\x00\'\x00.\x00\x1e\x00\x14\x00\x17\x00\n\x00\x0f\x00$\x00%\x003\x00/\x00\x1d\x00\x17\x00\t\x00\x1d\x00(\x00\'\x00:\x00B\x00I\x00;\x00.\x004\x00?\x00>\x006\x007\x00)\x00"\x00-\x00+\x00-\x00$\x00\x1f\x00\x1d\x00\x15\x00\x1a\x00\x11\x00\x06\x00\x02\x00\x04\x00\n\x00\x14\x00\x1a\x00\x13\x00\x13\x00\t\x00\xfe\xff\xfa\xff\xf1\xff\xef\xff\xef\xff\xe3\xff\xdf\xff\xe1\xff\xd8\xff\x

b'\x1f\xfb\x9b\xfc\x05\xfeL\xffr\x00\x84\x01i\x02\x11\x03\xbf\x03\x88\x044\x05\xb0\x05\x1e\x06\x90\x06\xcf\x06\xfb\x06P\x07\xa3\x07\xad\x07\x8d\x07\x8e\x07t\x07\x1c\x07\xc4\x06h\x06\xd9\x05\x1b\x05\x87\x04\'\x04\xb0\x035\x03\xd1\x02Y\x02\xe2\x01\xc6\x01\xf8\x01\x00\x02\xdf\x01\xf7\x016\x02?\x02S\x02\xc8\x02\x1f\x03\xf0\x02\xe3\x02I\x03\x80\x03I\x03I\x03}\x03\x02\x030\x02%\x02c\x02\xb5\x01\xc2\x00\xa9\x00\xbd\x00\xe4\xffh\xff\x1f\x00\xea\xffa\xfe\xf5\xfd\x88\xff[\x00a\xff3\xff\x9e\x009\x01N\x00{\x00\x1b\x02\xa5\x02\xd7\x01\x1b\x02\xbb\x03\x9d\x04\x87\x04\xef\x04\x00\x06\x94\x06\xe7\x06\xf0\x07\x80\t\xd9\n\x9f\x0b\x92\x0c\x80\x0e\xad\x10]\x11\x82\x10Z\x100\x11\xc8\x10\x18\x0ff\x0eU\x0e\xf2\x0b(\x08d\x06\x97\x05\x84\x02E\xfet\xfc\x19\xfc\xfb\xf9}\xf7.\xf7T\xf7K\xf5\xd2\xf2n\xf2\x93\xf2!\xf1%\xef\xb0\xee\xc9\xee\xac\xed4\xec\xc2\xeb\x06\xec\xa7\xeb\xe9\xeax\xebA\xedU\xee\x84\xee\x07\xf0p\xf3\x01\xf6\xb4\xf6\xed\xf7b\xfa\x0f\xfc6\xfcd\xfd\x12\x00\xcd\x01\t\x02;\x02\xae\x02\xf9\x01\xc2\x00\x

b'\xcf\xf4-\xee\xb1\xeac\xe5+\xe0\xd8\xe0\xdf\xe8\xc7\xefm\xf0m\xf4.\xfb\xd8\xff~\x00\xf0\xfe\xdd\xfd\x84\xf9c\xf4\x19\xf0\xb1\xefx\xef~\xeeH\xef\xfe\xed\xe0\xef\xcd\xf2|\xf5\x99\xf9\xe2\xfa\x0c\xfa\x82\xf8\n\xf8\xcd\xf5\xc9\xf3B\xf40\xf3\xc3\xf4\xfe\xf6\xc6\xf9r\x00\x85\x03\xef\x00\x1a\x00\xf3\x01\xdf\x01\x11\x02s\x02$\x02{\xff0\xfaO\xf9\x86\xfb\xeb\xff\x92\x05W\x07\xe9\x07j\x08\xff\x07F\x06B\x05\t\x06F\x03\xc6\xffJ\xff\xbb\xfdv\xfc5\xfd$\xfe"\xfep\xfe\xe5\x00(\x01W\xffR\x00\xf7\x01\x1b\x01\xc6\x00\x92\x00\xa1\xfd\xd1\xfc\xcc\xfd\x13\xfe\xc0\xffs\x01f\x01\x1d\x00\xe9\x00j\x01\xfe\xff\xd6\x00\x08\x01\x9e\xffi\xffL\x00\xbc\x01\xed\x02\x80\x02\xf8\x01\x06\x03\xf8\x02\x14\x030\x05~\x06\\\x05\x96\x04M\x05\xc7\x03\xc3\x02V\x04\x9f\x05\x11\x07c\x065\x04s\x03?\x02\xcc\xffb\xff\x91\x01v\x01(\x00;\x01\xcb\x01\xff\x00{\x06\xfc\x14D&\xa7/h.\xbc-V-\x19&\xb8\x1c\x08\x17\x8b\x13\xab\x07v\xf4\xf7\xe7\x8b\xe5\x8c\xe5\xd8\xe0\x88\xe0G\xe7\xed\xefl\xf4@\xf5\x98\xfb\t\x01>\x02u\xfc\x0e\xf8!\xf8~\xf3\x12\

...

b'\x06\x00\x07\x00\x02\x00\xff\xff\xfe\xff\xff\xff\x00\x00\xfb\xff\xfb\xff\xfb\xff\xfd\xff\x02\x00\x00\x00\xfd\xff\xfb\xff\xfa\xff\xff\xff\x01\x00\x02\x00\x05\x00\x04\x00\xfe\xff\xf9\xff\xf6\xff\xf6\xff\xfa\xff\xfd\xff\xfb\xff\xfa\xff\xf9\xff\xf5\xff\xf4\xff\xf4\xff\xf1\xff\xf1\xff\xf1\xff\xf3\xff\xf4\xff\xf6\xff\xf7\xff\xf6\xff\xf5\xff\xf1\xff\xf0\xff\xf0\xff\xef\xff\xf2\xff\xf4\xff\xf7\xff\xf9\xff\xfb\xff\xfd\xff\xfd\xff\xff\xff\x00\x00\xfe\xff\xfd\xff\xfd\xff\xfb\xff\xfb\xff\xfd\xff\xfa\xff\xf9\xff\xf8\xff\xf5\xff\xf7\xff\xf5\xff\xf6\xff\xfd\xff\x05\x00\t\x00\n\x00\x08\x00\x06\x00\x08\x00\x0b\x00\n\x00\x0b\x00\x0e\x00\x0b\x00\x0b\x00\x0e\x00\x0f\x00\t\x00\x07\x00\x0b\x00\x05\x00\x01\x00\x02\x00\x03\x00\x03\x00\x07\x00\n\x00\x07\x00\x04\x00\x07\x00\x08\x00\x06\x00\x06\x00\x06\x00\x02\x00\x02\x00\x03\x00\x04\x00\x05\x00\x07\x00\n\x00\r\x00\x10\x00\x11\x00\x11\x00\x12\x00\x11\x00\r\x00\n\x00\x08\x00\x07\x00\x07\x00\x02\x00\x02\x00\x05\x00\x04\x00\xfe\xff\xfc\xff\xfd\xff\xfd\xff\xf9\xff

b'\xff\xff\x01\x00\x00\x00\xfb\xff\xf7\xff\xfa\xff\xf8\xff\xf5\xff\xf3\xff\xef\xff\xee\xff\xef\xff\xf1\xff\xf0\xff\xea\xff\xed\xff\xf1\xff\xf0\xff\xf2\xff\xf0\xff\xee\xff\xf0\xff\xf2\xff\xf1\xff\xed\xff\xf1\xff\xf6\xff\xf7\xff\xf6\xff\xf4\xff\xf5\xff\xf2\xff\xf2\xff\xf6\xff\xfa\xff\xf9\xff\xfd\xff\xff\xff\x00\x00\xfd\xff\xfa\xff\xfe\xff\x02\x00\x05\x00\x04\x00\x02\x00\x06\x00\x03\x00\x00\x00\x01\x00\xfb\xff\xf6\xff\xf7\xff\xf8\xff\xf4\xff\xef\xff\xf3\xff\xf9\xff\xfc\xff\x00\x00\x04\x00\x04\x00\x02\x00\x01\x00\xfd\xff\x01\x00\x03\x00\x01\x00\x02\x00\x05\x00\x05\x00\x06\x00\x0b\x00\x0c\x00\x0c\x00\n\x00\n\x00\x0b\x00\x05\x00\x04\x00\x04\x00\x03\x00\n\x00\r\x00\r\x00\r\x00\x0b\x00\t\x00\x08\x00\n\x00\r\x00\x10\x00\x10\x00\x0f\x00\n\x00\n\x00\x08\x00\x06\x00\x07\x00\x05\x00\x04\x00\x04\x00\x00\x00\xff\xff\xff\xff\x04\x00\x05\x00\x06\x00\n\x00\x05\x00\x00\x00\xfe\xff\xf6\xff\xf7\xff\xfe\xff\xfe\xff\xfc\xff\xf9\xff\xf8\xff\xfc\xff\xfc\xff\xf9\xff\xfa\xff\xfd\xff\xfe\xff\xfc\xff\xfd\xff\x00\x

b'\xf7\xff\xf9\xff\xfa\xff\xf8\xff\xfb\xff\xfb\xff\xfc\xff\xff\xff\xfc\xff\xfa\xff\xfd\xff\xfe\xff\x03\x00\n\x00\n\x00\x04\x00\x04\x00\x02\x00\xfd\xff\xfc\xff\xfe\xff\xfc\xff\xf9\xff\xfc\xff\xfd\xff\x00\x00\x02\x00\x00\x00\xfd\xff\xfe\xff\xfe\xff\xfc\xff\xff\xff\x02\x00\x06\x00\t\x00\x07\x00\x08\x00\x08\x00\x0b\x00\r\x00\r\x00\x0f\x00\x0e\x00\x10\x00\x14\x00\x11\x00\x0e\x00\n\x00\n\x00\n\x00\x07\x00\x10\x00\x11\x00\x11\x00\x17\x00\x15\x00\x15\x00\x16\x00\x13\x00\x0c\x00\x04\x00\x02\x00\x00\x00\xfe\xff\xfb\xff\xf9\xff\xfc\xff\xfe\xff\x00\x00\xfd\xff\xf9\xff\xf4\xff\xee\xff\xeb\xff\xec\xff\xeb\xff\xed\xff\xf0\xff\xef\xff\xef\xff\xef\xff\xef\xff\xf0\xff\xeb\xff\xea\xff\xec\xff\xe8\xff\xec\xff\xf0\xff\xef\xff\xf3\xff\xf3\xff\xf2\xff\xf1\xff\xf2\xff\xf5\xff\xfa\xff\xfb\xff\xfd\xff\x02\x00\x06\x00\x08\x00\t\x00\x0b\x00\n\x00\t\x00\x07\x00\xff\xff\xff\xff\x01\x00\x03\x00\x02\x00\x00\x00\x05\x00\x04\x00\x02\x00\xfe\xff\xfb\xff\xfa\xff\xf9\xff\xfa\xff\xfd\xff\x03\x00\x08\x00\x0f\x00\x10\x00\x0e

b'\xfe\xff\xfe\xff\xff\xff\x01\x00\x03\x00\x00\x00\x02\x00\x02\x00\xff\xff\x03\x00\x05\x00\x03\x00\x07\x00\x05\x00\x02\x00\x08\x00\t\x00\r\x00\x11\x00\x11\x00\r\x00\n\x00\x05\x00\xfe\xff\xfb\xff\xfd\xff\x00\x00\x02\x00\x03\x00\xff\xff\xfd\xff\xfe\xff\x01\x00\x04\x00\x06\x00\x0b\x00\n\x00\x08\x00\x07\x00\x07\x00\x05\x00\x04\x00\x02\x00\x01\x00\x02\x00\xff\xff\x00\x00\x04\x00\x06\x00\x03\x00\xfd\xff\xfa\xff\xf7\xff\xf5\xff\xf5\xff\xf9\xff\xf9\xff\xfa\xff\xfe\xff\xff\xff\xfe\xff\xff\xff\xff\xff\x00\x00\x02\x00\x05\x00\x03\x00\x02\x00\x04\x00\x04\x00\x07\x00\x08\x00\x04\x00\x02\x00\x01\x00\xfe\xff\xf9\xff\xf5\xff\xf7\xff\xf5\xff\xf5\xff\xf9\xff\xfb\xff\xff\xff\x04\x00\x03\x00\x00\x00\xf9\xff\xf7\xff\xf5\xff\xf5\xff\xf9\xff\xf8\xff\xf5\xff\xf4\xff\xf2\xff\xf3\xff\xf2\xff\xf0\xff\xf3\xff\xf9\xff\xfc\xff\xfe\xff\xfb\xff\xfe\xff\x03\x00\x00\x00\xff\xff\x00\x00\xff\xff\xff\xff\xff\xff\x01\x00\xfc\xff\xf9\xff\xfb\xff\xfa\xff\xf9\xff\xfa\xff\xf9\xff\xfb\xff\xfd\xff\x03\x00\t\x00\x0c\x00\x08\x00\x

KeyboardInterrupt: 